In [3]:
import zipfile

zip_file_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam.zip"
output_directory = "/teamspace/studios/this_studio/SpeechAssign2_Q1"

# Open the zip file
with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
    # Extract all the contents to the output directory
    zip_ref.extractall(output_directory)


In [4]:
import zipfile

zip_file_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam_csv.zip"
output_directory = "/teamspace/studios/this_studio/SpeechAssign2_Q1"

# Open the zip file
with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
    # Extract all the contents to the output directory
    zip_ref.extractall(output_directory)


In [5]:
!pip install s3prl

In [6]:
!pip install soundfile

In [9]:
import torch
import torchaudio
from s3prl.nn import S3PRLUpstream
import os
import numpy as np
from scipy.spatial.distance import cdist
from sklearn.metrics import roc_curve, auc
import soundfile as sf
from scipy.spatial.distance import cosine

# Set the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")




In [ ]:
# Load the Kathbath Dataset test set
test_audio_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio"
audio_files = sorted(os.listdir(test_audio_path))

In [8]:
import re
import os

pairs_file = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known_data.txt"
lines = open(pairs_file).read().splitlines()
audio_file = set()
reference_pairs = []
non_reference_pairs = []
diction = {}
for line in lines:
    parts = line.split('\t')  # Splitting based on tabs
    
    if len(parts) < 3:
        # Skip this line if it doesn't have all three parts
        continue

    label = int(parts[0])
    # ref_path+ = parts[1].replace("/nlsasfs/home/ai4bharat/gramesh/speechteam/e2e_data/pilot4_karya/aug_dc_data_raw/dc_data_clean_wav/malayalam/test/audio", "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio").replace(".wav", ".m4a")
    ref_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/" + parts[1].split('/')[-1].replace(".wav", ".m4a")
    print(ref_path)
    
    # non_ref_path = parts[2].replace("/nlsasfs/home/ai4bharat/gramesh/speechteam/e2e_data/pilot4_karya/aug_dc_data_raw/dc_data_clean_wav/malayalam/test/audio", "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio").replace(".wav", ".m4a")
    non_ref_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/" + parts[2].split('/')[-1].replace(".wav", ".m4a")

    # Check if at least one of the paths exists, and skip the line if not
    if not (os.path.exists(ref_path) or os.path.exists(non_ref_path)):
        continue
        
    if label == 1:
        reference_pairs.append((ref_path, non_ref_path))
    else:
        non_reference_pairs.append((ref_path, non_ref_path))
    audio_file.add(ref_path)
    audio_file.add(non_ref_path)
    # print(label, ref_path, non_ref_path)


/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931152457-985-m.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931276133-1007-m.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931121879-802-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931116531-474-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424930925124-763-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931329135-117-m.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424930848656-814-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931245114-763-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424930618462-653-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424933024179

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [9]:
len(audio_file)

1767

In [10]:
audio_file

{'/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931298419-355-m.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424933045430-985-m.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931350911-1132-m.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931077511-187-f.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424933030524-184-f.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424930377078-653-f.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424933027977-355-m.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424930787089-42-m.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424930925045-763-f.m4a',
 '/teamspace/studios/this_studio/SpeechAssign2_Q1/malay

In [11]:
# Load the model
model = S3PRLUpstream("wavlm_large")
model = model.to(device)
model.eval()

with torch.no_grad():
    wavs = torch.randn(2, 16000 * 2).to(device)
    wavs_len = torch.LongTensor([16000 * 1, 16000 * 2]).to(device)
    all_hs, all_hs_len = model(wavs, wavs_len)

for hs, hs_len in zip(all_hs, all_hs_len):
    # assert isinstance(hs, torch.FloatTensor)
    # assert isinstance(hs_len, torch.LongTensor)

    batch_size, max_seq_len, hidden_size = hs.shape
    assert hs_len.dim() == 1

/home/zeus/miniconda3/envs/cloudspace/lib/python3.10/site-packages/torch/nn/utils/weight_norm.py:28: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")
/home/zeus/miniconda3/envs/cloudspace/lib/python3.10/site-packages/torch/nn/functional.py:5109: UserWarning: Support for mismatched key_padding_mask and attn_mask is deprecated. Use same type for both instead.
  warnings.warn(


In [12]:
from s3prl.nn import Featurizer
featurizer = Featurizer(model).to(device)

In [13]:
hs, hs_len = featurizer(all_hs,all_hs_len)

In [14]:
hs.shape

torch.Size([2, 100, 1024])

In [15]:
print(hs.shape)

torch.Size([2, 100, 1024])


In [16]:
audio_file_list = list(audio_file)

In [17]:
!sudo apt install ffmpeg

Reading package lists... Done
Building dependency tree       
Reading state information... Done
ffmpeg is already the newest version (7:4.2.7-0ubuntu0.1).
0 upgraded, 0 newly installed, 0 to remove and 23 not upgraded.


In [18]:
!pip install pydub
!pip install ffprobe

In [19]:
from pydub import AudioSegment
a = audio_file_list[0]
sound = AudioSegment.from_file(a, format='m4a')

print(a)
# audio,_ = torchaudio.load(a)
# model.forward()

/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931298419-355-m.m4a


In [20]:
from tqdm import tqdm
# Function to extract features from audio files
def extract_features(model, audio_files):
    all_hs = []
    all_hs_len = []
    for audio_file in tqdm(audio_files, desc="Extracting features"):

        # Load audio file and convert to tensor
        # audio, sample_rate = torchaudio.load(audio_file)
        samples = AudioSegment.from_file(audio_file, format='m4a')
        audio = samples.get_array_of_samples()
        audio = np.array(audio,dtype = np.float32)
        audio = torch.from_numpy(audio)
        audio = audio.to(device)  # Move audio to the device
        
        # Preprocess audio if needed (e.g., resampling, normalization)
        # Reshape audio tensor to match expected dimensions
        if audio.dim() == 1:  # If mono-channel audio
            audio = audio.unsqueeze(0)  # Add batch dimension
        # Compute features from the audio using the model
        with torch.no_grad():
            hs, _ = model(audio, torch.LongTensor([audio.size(1)]))
            # print(hs)
            
            hs, hs_len = featurizer(hs,_)
            hs = hs.cpu().detach().numpy()
            # hs_len = hs_len.cpu()
            diction[audio_file] = hs
            # all_hs_len.append(hs_len)
            del audio
    # return all_hs


In [21]:
import warnings

# Ignore all warnings
warnings.filterwarnings("ignore")

In [22]:
# Extract features for reference pairs
extract_features(model, audio_file_list)

Extracting features: 100%|██████████| 1767/1767 [18:14<00:00,  1.61it/s]


In [33]:
# Assuming your_dictionary is already loaded from the pickle file

# Display the first 5 key-value pairs
count = 0
for key, value in diction.items():
    print(f"{key}: {value}")
    print(value[0].shape)
    print(value.mean(axis = 1).shape)
    count += 1
    if count == 5:
        break


/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424931298419-355-m.m4a: [[[-5.2964625  -2.1278543  -1.9505637  ... -2.4549012   9.329809
    0.06201962]
  [-2.0527306  -4.753642   -6.392847   ...  3.5281162   0.88961875
   -1.070651  ]
  [-2.8473186  -2.972863   -5.863109   ...  5.418172    1.7347106
   -1.5669037 ]
  ...
  [-0.5487162  -2.2871523  -0.4390097  ... -0.34549993  0.8411703
    0.01148671]
  [-2.602208   -4.0162783   1.0852903  ... -2.0532424   8.753653
    0.11041689]
  [-2.602208   -4.0162783   1.0852903  ... -2.0532424   8.753653
    0.11041689]]]
(1293, 1024)
(1, 1024)
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio/844424933045430-985-m.m4a: [[[-6.875941   -1.0012908  -5.7338777  ... -1.7916026   7.9924383
    2.3276885 ]
  [-2.999589   -2.0288103  -8.424623   ...  2.3024535   0.9655872
    1.218301  ]
  [-3.6040852  -1.4967911  -7.2607427  ...  4.3063025   1.0817058
    0.6447209 ]
  ...
  [-4.092199   -3.93254

In [36]:
# Compute cosine similarity between reference and non-reference pairs
cosine_similarity_scores1 = []
cosine_similarity_scores2 = []

# for ref_feature, non_ref_feature in zip(reference_features, non_reference_features):
for file1, file2 in tqdm(reference_pairs):
    feature1 = torch.tensor(diction[file1].mean(axis = 1))
    feature2 = torch.tensor(diction[file2].mean(axis = 1))
    # print(feature1, feature2)
    cosine_similarity = torch.nn.functional.cosine_similarity(feature1, feature2)
    cosine_similarity_scores1.extend(cosine_similarity)

for file1, file2 in tqdm(non_reference_pairs):
    feature1 = torch.tensor(diction[file1].mean(axis = 1))
    feature2 = torch.tensor(diction[file2].mean(axis = 1))
    cosine_similarity = torch.nn.functional.cosine_similarity(feature1, feature2)
    cosine_similarity_scores2.extend(cosine_similarity)

# Combine cosine similarity scores and create labels
cosine_similarity_scores = cosine_similarity_scores1 + cosine_similarity_scores2
labels = [1] * len(cosine_similarity_scores1) + [0] * len(cosine_similarity_scores2)

# Compute ROC curve
fpr, tpr, thresholds = roc_curve(labels, cosine_similarity_scores)

# Compute EER
eer_threshold = thresholds[np.argmin(np.abs(fpr - (1 - tpr)))]
eer = fpr[np.argmin(np.abs(fpr - (1 - tpr)))]

# Report the EER
print("Equal Error Rate (EER): {:.4f}".format(eer))

100%|██████████| 25047/25047 [00:34<00:00, 718.14it/s]


Equal Error Rate (EER): 19.14%


In [38]:
# Report the EER
print("Equal Error Rate (EER): {:.4f}".format(eer))

Equal Error Rate (EER): 0.1914


In [39]:
del diction

In [40]:
del cosine_similarity_scores, cosine_similarity_scores1, cosine_similarity_scores2, non_reference_pairs, reference_pairs

In [39]:
import torch
import torchaudio
from s3prl.nn import S3PRLUpstream
import os
import numpy as np
from scipy.spatial.distance import cdist
from sklearn.metrics import roc_curve, auc
import soundfile as sf
from scipy.spatial.distance import cosine

# Set the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")




In [38]:
import zipfile

zip_file_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam_valid.zip"
output_directory = "/teamspace/studios/this_studio/SpeechAssign2_Q1"

# Open the zip file
with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
    # Extract all the contents to the output directory
    zip_ref.extractall(output_directory)


In [1]:
# Load the Kathbath Dataset test set
import re
import os

valid_audio_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio"
audio_files = sorted(os.listdir(valid_audio_path))

In [40]:
import re
import os

pairs_file = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid_data.txt"
lines = open(pairs_file).read().splitlines()
audio_file = set()
pairs = []

valid_diction = {}
for line in lines:
    parts = line.split('\t')  # Splitting based on tabs
    
    if len(parts) < 3:
        # Skip this line if it doesn't have all three parts
        continue

    label = int(parts[0])
    # ref_path+ = parts[1].replace("/nlsasfs/home/ai4bharat/gramesh/speechteam/e2e_data/pilot4_karya/aug_dc_data_raw/dc_data_clean_wav/malayalam/test/audio", "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio").replace(".wav", ".m4a")
    ref_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/" + parts[1].split('/')[-1].replace(".wav", ".m4a")
    print(ref_path)
    
    # non_ref_path = parts[2].replace("/nlsasfs/home/ai4bharat/gramesh/speechteam/e2e_data/pilot4_karya/aug_dc_data_raw/dc_data_clean_wav/malayalam/test/audio", "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/test_known/audio").replace(".wav", ".m4a")
    non_ref_path = "/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/" + parts[2].split('/')[-1].replace(".wav", ".m4a")

    # Check if at least one of the paths exists, and skip the line if not
    if not (os.path.exists(ref_path) or os.path.exists(non_ref_path)):
        continue
        
    if label == 1:
        pairs.append((ref_path, non_ref_path, 1))
    else:
        pairs.append((ref_path, non_ref_path, 0))
    audio_file.add(ref_path)
    audio_file.add(non_ref_path)
    # print(label, ref_path, non_ref_path)


/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424930787382-420-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424931023468-1132-m.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424930586158-474-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424931245142-763-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424933082922-1145-m.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424931332344-187-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424931327795-1132-m.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424933079589-184-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424930444389-474-f.m4a
/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424930510201-802-f.m4a
/teamspace/studios/this_studio/Speech

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [41]:
audio_file_list = list(audio_file)

In [42]:
from pydub import AudioSegment
a = audio_file_list[0]
sound = AudioSegment.from_file(a, format='m4a')

print(a)
# audio,_ = torchaudio.load(a)
# model.forward()

/teamspace/studios/this_studio/SpeechAssign2_Q1/malayalam/valid/audio/844424930343765-42-m.m4a


In [43]:
from tqdm import tqdm
# Function to extract features from audio files
def extract_features(model, audio_files):
    all_hs = []
    all_hs_len = []
    for audio_file in tqdm(audio_files, desc="Extracting features"):

        # Load audio file and convert to tensor
        # audio, sample_rate = torchaudio.load(audio_file)
        samples = AudioSegment.from_file(audio_file, format='m4a')
        audio = samples.get_array_of_samples()
        audio = np.array(audio,dtype = np.float32)
        audio = torch.from_numpy(audio)
        audio = audio.to(device)  # Move audio to the device
        
        # Preprocess audio if needed (e.g., resampling, normalization)
        # Reshape audio tensor to match expected dimensions
        if audio.dim() == 1:  # If mono-channel audio
            audio = audio.unsqueeze(0)  # Add batch dimension
        # Compute features from the audio using the model
        with torch.no_grad():
            hs, _ = model(audio, torch.LongTensor([audio.size(1)]))
            # print(hs)
            
            hs, hs_len = featurizer(hs,_)
            hs = hs.cpu().detach().numpy()
            # hs_len = hs_len.cpu()
            valid_diction[audio_file] = hs
            # all_hs_len.append(hs_len)
            del audio
    # return all_hs


In [6]:
import warnings

# Ignore all warnings
warnings.filterwarnings("ignore")

In [56]:
# Extract features for reference pairs
extract_features(model, audio_file_list)

Extracting features: 100%|██████████| 1768/1768 [18:14<00:00,  1.62it/s]


In [58]:
# Compute cosine similarity between reference and non-reference pairs
cosine_similarity_scores = []
labels = []

# for ref_feature, non_ref_feature in zip(reference_features, non_reference_features):
for file1, file2, label in tqdm(pairs):
    feature1 = torch.tensor(valid_diction[file1].mean(axis = 1))
    feature2 = torch.tensor(valid_diction[file2].mean(axis = 1))
    # print(feature1, feature2)
    cosine_similarity = torch.nn.functional.cosine_similarity(feature1, feature2)
    cosine_similarity_scores.extend(cosine_similarity)
    labels.append(label)

# Compute ROC curve
fpr, tpr, thresholds = roc_curve(labels, cosine_similarity_scores)

# Compute EER
eer_threshold = thresholds[np.argmin(np.abs(fpr - (1 - tpr)))]
eer = fpr[np.argmin(np.abs(fpr - (1 - tpr)))]

# Report the EER
print("Equal Error Rate (EER): {:.4f}".format(eer))

100%|██████████| 50000/50000 [01:08<00:00, 734.08it/s]


Equal Error Rate (EER): 0.2003


In [101]:
from s3prl.nn import Featurizer
# Load the model
model = S3PRLUpstream("wavlm_base_plus")
model = model.to(device)

featurizer = Featurizer(model).to(device)

In [102]:
from torch.utils.data import DataLoader, Dataset
class CustomDataset(Dataset):
    def __init__(self, dataframe):
        self.dataframe = dataframe

    def __len__(self):
        return len(self.dataframe)

    def __getitem__(self, idx):
        row = self.dataframe[idx]
        file1_path = row[0]
        file2_path = row[1]
        label = row[2]
        sample1 = AudioSegment.from_file(file1_path, format='m4a')
        sample2 = AudioSegment.from_file(file2_path, format='m4a')
        
        audio1 = sample1.get_array_of_samples()
        audio2 = sample2.get_array_of_samples()
        
        audio1 = np.array(audio1,dtype = np.float32)[:32000]
        # print(audio1[:32000].shape)
        audio2 = np.array(audio2,dtype = np.float32)[:32000]
        
        audio1 = torch.from_numpy(audio1)
        audio2 = torch.from_numpy(audio2)
        label = torch.tensor(label, dtype = torch.float)

        return audio1, audio2, label
        
def collate_fn( samples):
    return zip(*samples)

In [105]:
train_dataset = CustomDataset(pairs)
train_loader = DataLoader(train_dataset, batch_size = 16, num_workers = 8, shuffle = True,collate_fn = collate_fn)

In [106]:
# next(iter(train_loader))

In [107]:
import torch.optim as optim
from tqdm import tqdm

print(device)
# Define optimizer
optimizer = optim.Adam(model.parameters(), lr=0.0001)
loss_fn = torch.nn.BCELoss()

model.train()
# Number of epochs
num_epochs = 5

for epoch in range(num_epochs):
    total_loss = 0
    total_pairs = 0
    for data in tqdm(train_loader):
        ref1, ref2, label = list(data)
        ref1 = torch.stack(ref1).to(device)
        ref2 = torch.stack(ref2).to(device)
        # ref1 = [ref.to(device) for ref in ref1]
        # ref2 = [ref.to(device) for ref in ref2]
        label = torch.tensor(label).to(device)

        # print(len(ref1),ref1[0].shape)
        optimizer.zero_grad()
        seq_length = torch.LongTensor([ref1.size(1)  for i in range(1,ref1.size(0)+1)]).to(device)
        # print(seq_length,ref1.shape)
        hs1, _1 = model(ref1, seq_length)   
        # print(_1,"HH")
        hs2, _2 = model(ref2, seq_length)  
        # print(hs1[0].shape, 'H')
        hs1, _ = featurizer(hs1,_1)
        hs2, _ = featurizer(hs2,_2)
        # print(hs1.shape)
        
        hs1 = hs1.mean(axis = 1)
        hs2 = hs2.mean(axis = 1)
        # print(hs1.shape)
        cosine_sim = torch.cosine_similarity(hs1, hs2, dim=1)
        predicted_score = torch.sigmoid(cosine_sim)
        # label_tensor = torch.tensor(label)

        loss = loss_fn(predicted_score, label)
        total_loss += loss.item()
        total_pairs += 1

        loss.backward()
        optimizer.step()

    avg_loss = total_loss / total_pairs
    EER = avg_loss * 100
    print("Epoch [{}/{}], Equal Error Rate (EER): {:.2f}%".format(epoch+1, num_epochs, EER))


cuda


100%|██████████| 3125/3125 [46:09<00:00,  1.13it/s] 


Epoch [1/5], Equal Error Rate (EER): 53.62%


100%|██████████| 3125/3125 [45:54<00:00,  1.13it/s] 


Epoch [2/5], Equal Error Rate (EER): 51.79%


100%|██████████| 3125/3125 [44:18<00:00,  1.18it/s] 


Epoch [3/5], Equal Error Rate (EER): 51.50%


 26%|██▌       | 803/3125 [11:20<32:49,  1.18it/s]  


KeyboardInterrupt: 

In [ ]:
# Compute cosine similarity between reference and non-reference pairs
cosine_similarity_scores = []
labels = []

# for ref_feature, non_ref_feature in zip(reference_features, non_reference_features):
for file1, file2, label in tqdm(pairs):
    feature1 = torch.tensor(valid_diction[file1].mean(axis = 1))
    feature2 = torch.tensor(valid_diction[file2].mean(axis = 1))
    # print(feature1, feature2)
    cosine_similarity = torch.nn.functional.cosine_similarity(feature1, feature2)
    cosine_similarity_scores.extend(cosine_similarity)
    labels.append(label)

# Compute ROC curve
fpr, tpr, thresholds = roc_curve(labels, cosine_similarity_scores)

# Compute EER
eer_threshold = thresholds[np.argmin(np.abs(fpr - (1 - tpr)))]
eer = fpr[np.argmin(np.abs(fpr - (1 - tpr)))]

# Report the EER
print("Equal Error Rate (EER): {:.4f}".format(eer))